In [201]:
from datasets import load_from_disk
dataset = load_from_disk("../data/train_dataset/")
print(dataset)

DatasetDict({
    train: Dataset({
        features: ['__index_level_0__', 'answers', 'context', 'document_id', 'id', 'question', 'title'],
        num_rows: 3952
    })
    validation: Dataset({
        features: ['__index_level_0__', 'answers', 'context', 'document_id', 'id', 'question', 'title'],
        num_rows: 240
    })
})


In [202]:
dataset['train']['context'][0]

'미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다.\\n\\n미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다.\\n\\n미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05'

In [203]:
dataset['train']['answers'][10]['text']

['음독자살']

In [204]:
import re

def preprocess(text):
    text = re.sub(r'\n', " ", text)
    text = re.sub(r"\\n", " ", text)
    text = re.sub(r'#', " ", text)
    # text = re.sub(r'\'', " ", text) # \' 표시를 하지 않으면 순수 작은 따음표로 인식하지 않음
    
    text = re.sub(r"[“”‘’]", "\'", text)
    text = re.sub(r"[〈<＜「≪《『]", "<", text)
    text = re.sub(r"[〉>＞」≫》』]", ">", text)
    
    text = re.sub(r"\s+", " ", text)
    text = re.sub(r"[^a-zA-Z0-9가-힣ㄱ-ㅎㅏ-ㅣぁ-ゔァ-ヴー々〆〤一-龥<>()\s\.\?!》《≪≫\'<>〈〉:‘’%,『』「」＜＞・\"-“”∧]", "", text)
    return text

def answer_text_process(answer):
    text_list = answer['text']
    
    answer['text'] = list(map(preprocess, text_list))
    
    return answer
    

def run_preprocess(example):
    context = example["context"]
    start_ids = example["answers"]["answer_start"][0]
    
    before = context[:start_ids]
    after = context[start_ids:]
    
    process_before = preprocess(before)
    process_after = preprocess(after)
    process_data = process_before + process_after
    
    ids_move = len(before) - len(process_before)
    
    example["answers"] = answer_text_process(example["answers"])
    # example["answers"]['text'][0] = process_data(example['answers']['text'][0])
    example["context"] = process_data
    example["answers"]["answer_start"][0] = start_ids - ids_move
    
    return example

def check(data_list):
    for data in data_list:
        start_ids = data["answers"]["answer_start"][0]
        end_ids = start_ids + len(data["answers"]["text"][0])
        # print(data["answers"]["text"][0], data["context"][start_ids : end_ids])
        if data["answers"]["text"][0] != data["context"][start_ids : end_ids]:
            print("wrong")
            return
    print("good")
    

In [205]:
dataset['train'] = dataset['train'].map(run_preprocess)
dataset['validation'] = dataset['validation'].map(run_preprocess)
check(dataset['train'])
check(dataset['validation'])

Loading cached processed dataset at ../data/train_dataset/train/cache-8fe9da298578eee0.arrow
Loading cached processed dataset at ../data/train_dataset/validation/cache-64f10858b1416a31.arrow


good
good


In [206]:
dataset['train']['context'][0]
# dataset['validation']['context'][0]

'미국 상의원 또는 미국 상원(United States Senate)은 양원제인 미국 의회의 상원이다. 미국 부통령이 상원의장이 된다. 각 주당 2명의 상원의원이 선출되어 100명의 상원의원으로 구성되어 있다. 임기는 6년이며, 2년마다 50개주 중 1/3씩 상원의원을 새로 선출하여 연방에 보낸다. 미국 상원은 미국 하원과는 다르게 미국 대통령을 수반으로 하는 미국 연방 행정부에 각종 동의를 하는 기관이다. 하원이 세금과 경제에 대한 권한, 대통령을 포함한 대다수의 공무원을 파면할 권한을 갖고 있는 국민을 대표하는 기관인 반면 상원은 미국의 주를 대표한다. 즉 캘리포니아주, 일리노이주 같이 주 정부와 주 의회를 대표하는 기관이다. 그로 인하여 군대의 파병, 관료의 임명에 대한 동의, 외국 조약에 대한 승인 등 신속을 요하는 권한은 모두 상원에게만 있다. 그리고 하원에 대한 견제 역할(하원의 법안을 거부할 권한 등)을 담당한다. 2년의 임기로 인하여 급진적일 수밖에 없는 하원은 지나치게 급진적인 법안을 만들기 쉽다. 대표적인 예로 건강보험 개혁 당시 하원이 미국 연방 행정부에게 퍼블릭 옵션(공공건강보험기관)의 조항이 있는 반면 상원의 경우 하원안이 지나치게 세금이 많이 든다는 이유로 퍼블릭 옵션 조항을 제외하고 비영리건강보험기관이나 보험회사가 담당하도록 한 것이다. 이 경우처럼 상원은 하원이나 내각책임제가 빠지기 쉬운 국가들의 국회처럼 걸핏하면 발생하는 의회의 비정상적인 사태를 방지하는 기관이다. 상원은 급박한 처리사항의 경우가 아니면 법안을 먼저 내는 경우가 드물고 하원이 만든 법안을 수정하여 다시 하원에 되돌려보낸다. 이러한 방식으로 단원제가 빠지기 쉬운 함정을 미리 방지하는 것이다.날짜=2017-02-05'

In [60]:
n = -20

In [131]:
n += 20
for i in dataset['train']['answers'][n:n+20]:
    print(i['text'])
print(n)

['샤아']
['물']
['초록색']
['적혈구']
['브리타니아 해안']
['영국 시민권']
['스쿠아마에']
['<배은망덕>']
['화이트홀']
['요시다 성']
['상하이']
['곤막']
['교회']
['조선무선강습소']
['아이트라']
['인장']
['일본']
['조선중앙일보']
['에스타디오 아스테카']
['설법장면']
1400


In [132]:
!pwd

/opt/ml/code


In [209]:
dataset.save_to_disk('train_dataset')

In [216]:
import json

json_path = "/opt/ml/data/wikipedia_documents.json"

with open(json_path, 'r') as f:
    json_data = json.load(f)

for i in json_data:
    example = json_data[i]
    
    example['text'] = re.sub(r'\n', " ", example['text'])
    example['text'] = re.sub(r"\\n", " ", example['text'])
    example['text'] = re.sub(r'#', " ", example['text'])
    
    example['text'] = re.sub(r"[“”‘’]", "\'", example['text'])
    example['text'] = re.sub(r"[〈<＜「≪《『]", "<", example['text'])
    example['text'] = re.sub(r"[〉>＞」≫》』]", ">", example['text'])
    
    example['text'] = re.sub(r"\s+", " ", example['text'])
    example['text'] = re.sub(r"[^a-zA-Z0-9가-힣ㄱ-ㅎㅏ-ㅣぁ-ゔァ-ヴー々〆〤一-龥<>()\s\.\?!》《≪≫\'<>〈〉:‘’%,『』「」＜＞・\"-“”∧]", "", example['text'])
    
    # del example['corpus_source']
    # del example['url']
    # del example['domain']
    # del example['author']
    # del example['html']
    # del example['document_id']
    
    print(example)
                             
    json_data[i] = example

{'text': '이 문서는 나라 목록이며, 전 세계 206개 나라의 각 현황과 주권 승인 정보를 개요 형태로 나열하고 있다. 이 목록은 명료화를 위해 두 부분으로 나뉘어 있다. 첫 번째 부분은 바티칸 시국과 팔레스타인을 포함하여 유엔 등 국제 기구에 가입되어 국제적인 승인을 널리 받았다고 여기는 195개 나라를 나열하고 있다. 두 번째 부분은 일부 지역의 주권을 사실상 (데 팍토) 행사하고 있지만, 아직 국제적인 승인을 널리 받지 않았다고 여기는 11개 나라를 나열하고 있다. 두 목록은 모두 가나다 순이다. 일부 국가의 경우 국가로서의 자격에 논쟁의 여부가 있으며, 이 때문에 이러한 목록을 엮는 것은 매우 어렵고 논란이 생길 수 있는 과정이다. 이 목록을 구성하고 있는 국가를 선정하는 기준에 대한 정보는 "포함 기준" 단락을 통해 설명하였다. 나라에 대한 일반적인 정보는 "국가" 문서에서 설명하고 있다.', 'title': '나라 목록'}
{'text': '이 목록에 실린 국가 기준은 1933년 몬테비데오 협약 1장을 참고로 하였다. 협정에 따르면, 국가는 다음의 조건을 만족해야 한다. * (a) 영속적인 국민 * (b) 일정한 영토 * (c) 정부 * (d) 타국과의 관계 참여 자격. 특히, 마지막 조건은 국제 공동체의 참여 용인을 내포하고 있기 때문에, 다른 나라의 승인이 매우 중요한 역할을 할 수 있다. 이 목록에 포함된 모든 국가는 보통 이 기준을 만족하는 것으로 보이는 자주적이고 독립적인 국가이다. 하지만 몬테비데오 협약 기준을 만족하는지의 여부는 많은 국가가 논쟁이 되고 있는 실정이다. 또한, 몬테비데오 협약 기준만이 국가 지위의 충분한 자격이든 아니든, 국제법의 견해 차이는 존재할 수 있다. 이 물음에 대한 다른 이론에 대한 고리는 아래에서 볼 수 있다. 위 기준에 논거하여 이 목록은 다음 206개 국가를 포함하고 있다. * 일반 국제 승인을 받은 195개 자주 국가. ** 유엔 가입 국가 193개 ** 성좌의 명칭으로 유엔에서 국제 승인을 받은

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



{'text': '에너지 절약(Energy conservation)은 효율적 사용 또는 소비의 절감 등으로 사용하는 에너지의 양을 줄이는 것이다. 에너지의 절약을 통해 재정 절약, 환경의 가치, 인류의 편의의 향상을 도모할 수 있다. 에너지의 직접적인 소비자인 개인이나 단체는 에너지 비용의 절감을 위해 에너지를 절약하려 한다. 산업과 상업의 소비자는 효율을 개선하여 이익을 극대화하려 한다. 에너지 절약은 에너지 정책의 중요한 요소이다. 에너지를 절약함으로써 인구증가에 따른 에너지 비용을 감소시키며, 새로운 발전소를 건설하거나 에너지를 수입할 필요가 없도록 한다. 에너지 절약은 에너지 부족에 대한 최선의 경제적인 해결책이 되기도 한다. 에너지 배출을 줄이면 기후 변화의 폭을 줄이는 데 큰 도움이 된다. 에너지를 절약하면 다시 만들어낼 수 없는 자원을 재생 가능 에너지로 대체하는 작업이 용이해진다. 에너지 절약은 종종 에너지 부족의 가장 경제적인 해결책이 되며, 에너지 생산을 늘리는 것보다는 환경 친화적이다.', 'title': '에너지 절약'}
{'text': '일반적으로 알려져 있는 비용대비효과를 높일 수 있는 방법은 다음과 같다. * 불필요한 기기는 사용하지 않는다. * 온도, 습도 등의 설정을 점검하고, 운용 방법을 개선한다. * 제조업 등에서는 공정, 제조방법을 점검한다. * 설비, 기기의 보수, 효율적인 설비로의 교체 * 전력을 가능한 한 절약한다. 이 밖에도 에너지를 줄일 수 있는 방법은 여러 가지가 있다. * 쓰지 않는 플러그는 뽑아 놓고, 쓰지 않는 조명은 꺼두어야 한다. 일정 시간이 지나면 기기로의 전기 공급이 끊기는 플러그 타이머 따위의 상품이 존재한다. * 가까운 거리는 자동차, 엘레베이터, 에스컬레이터 따위를 이용하기보다는 걸어다니는 것이 좋다.걷기 자체도 활기차게 걸을수록 그 자체로 훌륭한 운동이며, 특히 계단 오르기는 허벅지의 근육을 자극하여 운동 효과도 크지만, 올바르지 않은 방식으로 장기간 계단 오르기를 할 경우 관절에 해로울 수 있

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



{'text': '부파불교의 설일체유부의 논서 <아비달마품류족론> 제6권에 따르면,세우 조, 현장 한역|T.1542|loc=제6권. p. T26n1542_p0714a15 - T26n1542_p0714a16. 유견법과 무견법|ps"有見法云何謂一處無見法云何謂十一處" : 유견법(有見法)은 일체법을 이루는 12처(十二處) 가운데 1처를 말한다. 즉, 색처(色處)를 말한다. : 무견법(無見法)은 일체법을 이루는 12처(十二處) 가운데 11처를 말한다. 즉, 색처(色處)를 제외한 나머지 안처(眼處) 이처(耳處) 비처(鼻處) 설처(舌處) 신처(身處) 의처(意處) 성처(聲處) 향처(香處) 미처(味處) 촉처(觸處) 법처(法處)의 11처를 말한다.', 'title': '유견법과 무견법'}
{'text': '부파불교의 설일체유부의 논서 <아비달마구사론> 제2권에 따르면, : 유견법(有見法)은 일체법을 이루는 18계(十八界) 가운데 1계인 색계(色界)를 말한다. 색계가 유견(有見)인 이유는 이러한 색(色: 즉, 각각의 현색과 형색)과 저러한 색의 차별을 드러내어 나타낼[示現] 수 있기 때문이다. 그리고 이러한 색과 저러한 색의 차별을 드러내어 나타낼[示現] 수 없으면 무견(無見)이라고 말할 수 있다. : 무견법(無見法)은 일체법을 이루는 18계(十八界) 가운데 색계(色界)를 제외한 나머지 모든 계(界)들을 말한다. 즉, 안계(眼界) 이계(耳界) 비계(鼻界) 설계(舌界) 신계(身界) 의계(意界) 성계(聲界) 향계(香界) 미계(味界) 촉계(觸界) 법계(法界) 안식계(眼識界) 이식계(耳識界) 비식계(鼻識界) 설식계(舌識界) 신식계(身識界) 의식계(意識界)의 17계를 말한다.', 'title': '유견법과 무견법'}
{'text': '대승불교의 중관학파의 논서 <대지도론> 제20권에 따르면, : 고타마 붓다는 색(色)에 가견유대색(可見有對色) 불가견유대색(不可見有對色) 불가견무대색(不可見無對色)의 3종색(三種色)이 있다고 설하였다. 즉, 색경에 속한 모든 법들을 이들 3종으로 분류할 수 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




{'text': '황전환경로(transsulfuration pathway) 또는 TS경로는 중간 시스타티오닌(cystathionine)을 통해 시스테인(cysteine)과 호모시스테인(homocysteine)의 상호 전환을 포함하는 대사 경로이다. 이것은 아세틸 또는 숙시닐 그룹(acetyl 또는 succinyl group)을 유리 황화물로 대체한다. 이는 cysK 또는 cysM 인코딩 시스테인 합성효소(cysteine synthase) 및 metZ 또는 metY 인코딩 호모시스테인 합성효소(homocysteine synthase)를 통해 시스테인 또는 호모시스테인 합성 및 사용을 위한 것으로 이와는 달리 황화수소(sulfide) 또는 메탄티올(methanethiol)을 사용하는 황산화 직접 경로(direct-sulfurylation pathway)와 대조된다. 순방향 및 역방향에서의 두 가지 TS(transsulfurylation) 경로가 알려져 있다.', 'title': '황전환경로'}
{'text': '순방향 경로는 대장균(Escherichia coli,E coli) 및 바실러스 서브틸리스(Bacillus subtilis) 와 같은 여러 박테리아에 존재하며 시스테인에서 호모시스테인(S-메틸 그룹을 갖는 메티오닌 전구체)으로의 티올 그룹의 이동을 포함한다. 호모세린(homeserine)의 아세틸 또는 숙시닐 그룹을 티올 그룹을 통해 시스테인으로 대체하여 시스타티오닌(E. coli에서 metB 및 B. subtilis에서 metI에 의해 코딩되는 시스타티오닌 γ-신타아제(cystathionine gamma-synthase)에 의해 촉매 됨)은 분자의 호모시스테인 부분의 β-제거(β-elimination)에 의해 절단되어 불안정한 아미노산을 남긴다. 이 산은 물에 의해 촉발되어 피루베이트(pyruvate)와 암모니아(ammonia)를 형성한다.(metC로 인코딩된 시스타티오닌 β-리에이스(cystathionine β-lyase) 에 의해 촉매 됨) 한편 황전

In [138]:
for v in json_data.values():
    print(v['text'])

이 문서는 나라 목록이며, 전 세계 206개 나라의 각 현황과 주권 승인 정보를 개요 형태로 나열하고 있다. 이 목록은 명료화를 위해 두 부분으로 나뉘어 있다. 첫 번째 부분은 바티칸 시국과 팔레스타인을 포함하여 유엔 등 국제 기구에 가입되어 국제적인 승인을 널리 받았다고 여기는 195개 나라를 나열하고 있다. 두 번째 부분은 일부 지역의 주권을 사실상 (데 팍토) 행사하고 있지만, 아직 국제적인 승인을 널리 받지 않았다고 여기는 11개 나라를 나열하고 있다. 두 목록은 모두 가나다 순이다. 일부 국가의 경우 국가로서의 자격에 논쟁의 여부가 있으며, 이 때문에 이러한 목록을 엮는 것은 매우 어렵고 논란이 생길 수 있는 과정이다. 이 목록을 구성하고 있는 국가를 선정하는 기준에 대한 정보는 "포함 기준" 단락을 통해 설명하였다. 나라에 대한 일반적인 정보는 "국가" 문서에서 설명하고 있다.
이 목록에 실린 국가 기준은 1933년 몬테비데오 협약 1장을 참고로 하였다. 협정에 따르면, 국가는 다음의 조건을 만족해야 한다. * (a) 영속적인 국민 * (b) 일정한 영토 * (c) 정부 * (d) 타국과의 관계 참여 자격. 특히, 마지막 조건은 국제 공동체의 참여 용인을 내포하고 있기 때문에, 다른 나라의 승인이 매우 중요한 역할을 할 수 있다. 이 목록에 포함된 모든 국가는 보통 이 기준을 만족하는 것으로 보이는 자주적이고 독립적인 국가이다. 하지만 몬테비데오 협약 기준을 만족하는지의 여부는 많은 국가가 논쟁이 되고 있는 실정이다. 또한, 몬테비데오 협약 기준만이 국가 지위의 충분한 자격이든 아니든, 국제법의 견해 차이는 존재할 수 있다. 이 물음에 대한 다른 이론에 대한 고리는 아래에서 볼 수 있다. 위 기준에 논거하여 이 목록은 다음 206개 국가를 포함하고 있다. * 일반 국제 승인을 받은 195개 자주 국가. ** 유엔 가입 국가 193개 ** 성좌의 명칭으로 유엔에서 국제 승인을 받은 국가: 바티칸 시국 ** 팔레스타인지역에 위치하며 유엔 영구 옵서버 국

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



속물 효과(俗物效果, Snob Effect)는 특정 제품에 대한 소비가 증가하게 되면 그 제품의 수요가 줄어드는 현상을 일컫는다. 또한 속물 효과는 네트워크 효과(Network Effect)의 일환이다. '한정 판매'는 소비자의 이런 심리를 이용한 판매자의 전술이다. 또한 Snob은 영어로 속물이라는 뜻인데, 다른 사람과 차이를 두고 싶은 속물처럼 타인과의 차별화를 위해 소비하는 현상을 말한다. 비슷한 말로는 백로 효과 등이 있으며, 반대되는 말로는 편승 효과 등이 있다. 백로 효과는 특정 상품에 많은 사람이 몰리면 희소성이 떨어져 차별화를 위해 다른 상품을 구매하려는 현상을 말하고, 우아한 백로처럼 남들과 다르게 보이려는 심리를 반영한다고 해서 백로 효과라고 한다. 다수의 소비자가 구매할 경우 오히려 그 제품에 대한 수요가 줄어드는 현상을 뜻하는 '속물 효과'는 명품 소비로 대변되는 과시적 소비는 물론, 좀 더 자신을 차별화하기 위한 개성을 추구하는 소비 효과이기도 하다. 사회적 지위나 재산을 숭배하는 사람을 지칭하는 snob 이란 단어가 의미하는 것처럼, '속물 효과'는 사람들이 가진 속물 근성의 하나로 표출되는 과시적 소비 욕구를 나타낸다. 그리고 100년 전통 스위스 명품 [[시계] 라고 허위 광고를 한 '빈센트 앤 코' 사건이나 세계 상위 1%의 여성들을 타깃으로 삼는 명품 화장품이라고 과장 광고를 한 '쓰리랩(3LAB)' 사건 등이 '속물 효과'의 예가 될 수 있다.
1995년 3월 25일에 열린 포항과의 리그컵 경기에서 울산 복귀전을 치렀으며 이 경기에서 멀티골을 넣으며 화려한 복귀를 알렸다. 4월 5일에 열린 LG 치타스와의 경기에서도 멀티골을 넣었다. 1995시즌 리그컵에서 6골을 넣으며 아디다스컵 득점왕을 차지했다. 컵대회 이후 치뤄진 리그에서는 5월 10일에 열린 LG 치타스와의 경기에서 첫 골을 넣었다. 6월 21일에 열린 전남과의 경기에서 후반 종료 직전 득점에 성공하며 팀의 1-0 승리를 이끌었다. 8월 23일에 열린 전북 다이노스와의

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




피청구인(경찰청장)은 노무현 전 대통령이 서거하자 고인을 조무하고자 덕수궁 대한문 앞 시민 분향소를 찾은 사람들이 그 건너편에 있는 서울광장에서 불법, 폭력, 집회나 시위를 개최하는 것을 막기 위하여 경찰버스들로 서울광장을 둘러싸 소위 차벽을 만드는 방법으로 서울광장에 출입하는 것을 제지하였다. 서울특별시민인 청구인들은 서울광장을 가로질러 통행하려고 하다가 서울광장을 둘러싼 경찰버스들에 의하여 만들어진 차변에 의하여 통행하지 못하게 되자 피청구인의 이와 같은 통행제지행위가 청구인들의 거주, 이전의 자유와 공물이용권 및 일반적 행동자유권을 침해한다고 주장하면서 그 위헌확인을 구하는 이 사건 헌법소원심판청구를 하였다.
이 사건 통행제지행위는 개별적인 집회를 금지하는 것을 넘어서서 서울광장에서 개최될 여지가 있는 일체의 집회를 금지할 뿐만 아니라 더 나아가서 일반시민들인 청구인들의 서울광장에서의 통행조차 금지한 것이여서 전면적이고 광범위하며 극단적인 조치이다. 필요한 최소한의 조치였다고 보기 어렵다. 서울광장의 몇 군데라도 통로를 개설하여 통제 하에 출입하게 하거나 대규모의 불법, 폭력 집회가 행해질 가능성이 적은 시간대라든지 서울광장 인근 건물에의 출근이나 왕래가 많은 오전 시간대에는 일부 통제를 풀 수 있다. 따라서 법익의 균형성 요건도 충족하지 못한다.
장룡식(張龍植, 1954년 6월 8일 ~ )은 조선민주주의인민공화국의 지휘자 겸 작곡.편곡자이다.장룡식은 현재 조선인민군공훈국가합창단에서 단장 겸 수석 지휘자로 활동하고 있다. 장룡식은 지휘 외에 작곡도 전공하여 보천보전자악단과 만수대예술단에서 지휘자 겸 작곡가 및 편곡가로 활동하던 인물로 알려져 있으며 현재는 조선인민군공훈국가합창단의 수석 지휘자 겸 단장 직책을 수행하고 있다. 장룡식은 북한 조선국립교향악단 음악창작과 음악형상수준을 새로운 경지에 올린 관록있는 지휘자로 북한 내에서 유명한 인물이다.또한 조선국립교향악단 수석 지휘자로 부임한 뒤에도 장룡식은 기존의 관현악곡들 외에 자신이 직접 편곡,창작한 성악

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




이 벽화는 무위사의 주불전인 극락보전 불단 뒤편 후불벽면에 그린 아미타여래삼존도로 화면 중앙의 아미타불을 중심으로 관음·지장보살을 좌우에 배치하고, 상단 구름 속에 상반신 만을 표현한 여섯 구의 나한상과 2구의 화불을 배치한 간단한 구도와 형식을 보여준다. 이곳에서는 일반적인 관음·내세지의 아미타삼존형식을 탈피하여 고려 후기부터 유행한 아미타불과 관음·지장보살의 삼존으로 구성되어 있는데, 이는 구복적인 정토신앙이 강하게 반영된 도상으로 조선 초기 수륙사(水陸社)로 지정된 무위사의 사격(寺格)과 잘 부합하는 도상으로 여겨진다. 특히 이 벽화는 화면 좌우 하단에 묵서로 씌어진 화기를 통하여 1476년(조선 성종7)에 군부인, 전직현감, 대선사를 비롯한 수십 명의 지역 유력자들이 불화제작에 참여하였다는 사실과 해련(海連)비구에 의해 벽화가 그렸음을 알 수 있다. 따라서 이 벽화는 제작시기와 조성 주체, 그리고 조성한 작가를 정확히 알 수 있다는 데서 조선 초기 불화 연구에 있어서 기준이 되는 중요한 작품이다. 양식적으로도 이 벽화는 고려후기 불화양식을 계승하면서도 조선 초기 새롭게 대두된 양식을 반영하고 있는 조선 전기 불화를 대표하는 유일한 벽화이다. 더구나 굵고 가는 선과 밝고 부드러운 색채를 자유자재로 구사하여 생동감 넘치는 종교 예술로 승화시킨 최고의 걸작품으로 평가된다. 특히, 수륙사 지정이라는 무위사의 역사적 사실과 잘 부합하는 국내에서 가장 오래된 "아미타여래삼존벽화"라는 점에서 그 가치는 더욱 크다 하겠다.
2011년 장민호는 '사랑해 누나'라는 곡을 발표하며 트로트가수로 첫 발을 내디뎠다. 트로트 가수로 활동하던 중 2012년 하반기 KBS2 '내생애 마지막 오디션'라는 오디션 프로그램에 출연해 가수 렌과 결성한 2인조 '렌미노'로 우승을 하기도 했다. 당시 '내 생애 마지막 오디션'은 대형 기획사 싸이더스HQ에서 우승팀을 중심으로 5인조 그룹을 만든다는 기획으로 준비된 프로그램이었기에 장민호는 싸이더스HQ로부터 팀 구성을 위해 현 소속사에서 나와

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [217]:
with open(json_path, 'w') as outfile:
    json.dump(json_data, outfile)

In [218]:
import json

json_path = "/opt/ml/data/wikipedia_documents.json"

with open(json_path, 'r') as f:
    json_data = json.load(f)

In [229]:
i=-1

In [237]:
i+=1
print(json_data[str(i)]['text'])

일본어 표기에 많이 쓰이는 올림문자 (후리가나)는 그대로 올려쓰지 않고 ''나 '<>'로 표시한다. 올림문자를 <> 로 묶거나 로 올릴 문자열을 특정하는 방식은 일본 시각장애인 독서지원협회 (BBA) 의 원문입력 수칙에 따른 것이다. 이 같은 방식을 예시로 들자면 다음과 같다. :青空文庫<ぶんこ> 아오조라 문고 라고 표기했다면 'ぶんこ' (분코)라는 올림표기가 '文庫' 부분에 걸려 있는 것이다. 다만, :本日は晴天<せいてん>なり 오늘은 맑은 하늘. 처럼 올림표기를 쓸 한자가 가나로 충분히 구분된다면 를 써서 분리할 필요가 없으므로 쓰지 않는다. 또한, :ブルースカイ<青空> 블루스카이 ("청공") 처럼 가나에 올림표기를 강제로 쓰는 것도 가능하다.


In [238]:
from datasets import load_from_disk
dataset = load_from_disk("data/train_dataset/")
print(dataset)

json_path = "/opt/ml/code/data/wikipedia_documents.json"

with open(json_path, 'r') as f:
    json_data = json.load(f)

DatasetDict({
    train: Dataset({
        features: ['__index_level_0__', 'answers', 'context', 'document_id', 'id', 'question', 'title'],
        num_rows: 3952
    })
    validation: Dataset({
        features: ['__index_level_0__', 'answers', 'context', 'document_id', 'id', 'question', 'title'],
        num_rows: 240
    })
})
